# DATA COLLECTION AND PREPROCESSING:

In [80]:
from pathlib import Path # convenient way to deal w/ paths
import plotly.graph_objects as go # creates plots
import numpy as np # standard for data processing
import pandas as pd # standard for data processing
import json # we have anomalies' timestamps in json format

In [81]:
# Path to the whole data from NAB git repository
nab = Path.cwd()/'NAB'

# This folder contains all files w/ metrics
data_path = nab/'data'

# There is also separate json file 
# w/ timestamps of anomalies in files w/ metrics
labels_filepath = nab/'labels/combined_labels.json'

# Path from data folder to the training file
training_filename = 'realAWSCloudwatch/rds_cpu_utilization_cc0c53.csv'

# Path from data folder to the validation file
valid_filename = 'realAWSCloudwatch/rds_cpu_utilization_e47b3b.csv'

In [82]:
with open(labels_filepath, 'r') as f:
    anomalies_timestamps = json.load(f)

In [83]:
train = pd.read_csv(data_path/training_filename)
valid = pd.read_csv(data_path/valid_filename)
train.head()

timestamp  value
0  2014-02-14 14:30:00  6.456
1  2014-02-14 14:35:00  5.816
2  2014-02-14 14:40:00  6.268
3  2014-02-14 14:45:00  5.816
4  2014-02-14 14:50:00  5.862

In [84]:
from sklearn.preprocessing import StandardScaler

# Let's make it function for further usage
def parse_and_standardize(df: pd.DataFrame, scaler: StandardScaler = None):
    df['timestamp'] = pd.to_datetime(df['timestamp'])
    df['stand_value'] = df['value']
    if not scaler:
        scaler = StandardScaler()
        scaler.fit(df['stand_value'].values.reshape(-1, 1))
    df['stand_value'] = scaler.transform(df['stand_value'].values.reshape(-1, 1))
    return scaler

data_scaler = parse_and_standardize(train)
parse_and_standardize(valid, data_scaler)

StandardScaler(copy=True, with_mean=True, with_std=True)

In [85]:
train_anomalies = train[train['timestamp'].isin(anomalies_timestamps[training_filename])]
valid_anomalies = valid[valid['timestamp'].isin(anomalies_timestamps[valid_filename])]
train_anomalies

timestamp    value  stand_value
3080 2014-02-25 07:15:00  25.1033     4.652449
3579 2014-02-27 00:50:00  19.1650     3.026441

In [86]:
# Prepare layout w/ titles
layout = dict(xaxis=dict(title='Timestamp'), yaxis=dict(title='CPU Utilization')) 

# Create the figure for plotting the data
fig = go.Figure(layout=layout) 

# Add non-anomaly data to the figure
fig.add_trace(go.Scatter(x=train['timestamp'], y=train['value'], 
                         mode='markers', name='Non-anomaly',
                         marker=dict(color='blue')))

# Add anomaly data to the figure
fig.add_trace(go.Scatter(x=train_anomalies['timestamp'],
                         y=train_anomalies['value'], 
                         mode='markers', name='Anomaly',
                         marker=dict(color='green', size=13)))

In [87]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=valid['timestamp'], y=valid['value'], 
                         mode='markers', name='Non-anomaly',
                         marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=valid_anomalies['timestamp'],
                         y=valid_anomalies['value'], 
                         mode='markers', name='Anomaly',
                         marker=dict(color='green', size=13)))

# ARIMA MODEL:

In [88]:
import statsmodels.api as sm
from itertools import product
import warnings
warnings.filterwarnings('ignore')

In [89]:
def write_predict(train_df: pd.DataFrame, valid_df: pd.DataFrame):
    # Initial approximation of parameters
    Qs = range(0, 2)
    qs = range(0, 3)
    Ps = range(0, 3)
    ps = range(0, 3)
    D=1
    d=1
    parameters = product(ps, qs, Ps, Qs)
    parameters_list = list(parameters)
    
    # Best Model Selection
    results = []
    best_aic = float("inf")
    for param in parameters_list:
        try:
            model=sm.tsa.statespace.SARIMAX(
                train_df.value, order=(param[0], d, param[1]),
                seasonal_order=(param[2], D, param[3], 12),
                initialization='approximate_diffuse'
                ).fit()
        except ValueError:
            print('wrong parameters:', param)
            continue
        aic = model.aic
        if aic < best_aic:
            best_model = model
            best_aic = aic
            best_param = param
        results.append([param, model.aic])
    
    # Writing of the predictions for training data
    train_df['predict'] = best_model.predict()
    train_df['predict'].fillna(0, inplace=True)
    
    # Writing of the predictions for validation data
    best_model_valid = sm.tsa.statespace.SARIMAX(
        valid_df.value, order=(best_param[0], d, best_param[1]),
        seasonal_order=(best_param[2], D, best_param[3], 12),
        initialization='approximate_diffuse'
        ).fit()
    valid_df['predict'] = best_model_valid.predict()
    valid_df['predict'].fillna(0, inplace=True)
    

# Calling of the function
write_predict(train, valid)

In [90]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=train['timestamp'], y=train['value'], 
                         mode='markers',name='ground truth',
                         marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=train['timestamp'],
                         y=train['predict'], 
                         mode='markers',name='predicted values',
                         marker=dict(color='green')))

In [91]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=valid['timestamp'], y=valid['value'], 
                         mode='markers',name='ground truth',
                         marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=valid['timestamp'],
                         y=valid['predict'], 
                         mode='markers',name='predicted values',
                         marker=dict(color='green')))

# CNN MODEL:

In [117]:
# PyTorch itself
import torch 
import tqdm
# Dataset - the base class to be inherited
from torch.utils.data import Dataset, DataLoader 
# We will need DataLoader later for the training process

In [118]:
class CPUDataset(Dataset):
    def __init__(self, data: pd.DataFrame, size: int, 
                 step: int = 1):
        self.chunks = torch.FloatTensor(data['stand_value']).unfold(0, size+1, step)
        self.chunks = self.chunks.view(-1, 1, size+1)
    def __len__(self):
        return self.chunks.size(0)
    
    def __getitem__(self, i):
        x = self.chunks[i, :, :-1]
        y = self.chunks[i, :, -1:].squeeze(1)
        return x, y

In [119]:
n_factors = 10
train_ds = CPUDataset(train, n_factors)
valid_ds = CPUDataset(valid, n_factors)

In [120]:
# here PyTorch has all neural net functions and activations
import torch.nn as nn

def conv_layer(in_feat, out_feat, kernel_size=3, stride=1,
               padding=1, relu=True):
    res = [
        nn.Conv1d(in_feat, out_feat, kernel_size=kernel_size,
                  stride=stride, padding=padding, bias=False),
        nn.BatchNorm1d(out_feat),
    ]
    if relu:
        res.append(nn.ReLU())
    return nn.Sequential(*res)

In [121]:
class ResBlock(nn.Module):
    def __init__(self, in_feat, out_feat):
        super().__init__()
        self.in_feat, self.out_feat = in_feat, out_feat
        self.conv1 = conv_layer(in_feat, out_feat)
        self.conv2 = conv_layer(out_feat, out_feat, relu=False)
        if self.apply_shortcut:
            self.shortcut = conv_layer(in_feat, out_feat,
                                       kernel_size=1, padding=0,
                                       relu=False)
    
    def forward(self, x):
        out = self.conv1(x)
        if self.apply_shortcut:
            x = self.shortcut(x)
        return x + self.conv2(out)
    
    @property
    def apply_shortcut(self):
        return self.in_feat != self.out_feat

In [122]:
class AdaptiveConcatPool1d(nn.Module):
    def __init__(self):
        super().__init__()
        self.ap = nn.AdaptiveAvgPool1d(1)
        self.mp = nn.AdaptiveMaxPool1d(1)
    
    def forward(self, x): 
        return torch.cat([self.mp(x), self.ap(x)], 1)

In [123]:
class CNN(nn.Module):
    def __init__(self, out_size):
        super().__init__()
        self.base = nn.Sequential(
            ResBlock(1, 8), #shape = batch, 8, n_factors
            ResBlock(8, 8), 
            ResBlock(8, 16), #shape = batch, 16, n_factors
            ResBlock(16, 16),
            ResBlock(16, 32), #shape = batch, 32, n_factors
            ResBlock(32, 32),
            ResBlock(32, 64), #shape = batch, 64, n_factors
            ResBlock(64, 64),
        )
        self.head = nn.Sequential(
            AdaptiveConcatPool1d(), #shape = batch, 128, 1
            nn.Flatten(),
            nn.Linear(128, out_size)
        )
        
    def forward(self, x):
        out = self.base(x)
        out = self.head(out)
        return out

In [124]:
def train_model(model: CNN, dataloaders: dict, optimizer: torch.optim.Optimizer, 
                scheduler, criterion, device: torch.device, epochs: int):
    losses_data = {'train': [], 'valid': []}
    model.to(device)
    
    # Loop over epochs
    for epoch in range(epochs):
        print(f'Epoch {epoch}/{epochs-1}')
        
        # Training and validation phases
        for phase in ['train', 'valid']:
            if phase == 'train':
                model.train()
            else:
                model.eval()

            running_loss = 0.
            running_total = 0.
            
            # Loop over batches of data
            for idx, batch in tqdm.tqdm(enumerate(dataloaders[phase]), 
                                   total=len(dataloaders[phase]), 
                                   leave=False
                                   ):
                x, y = batch
                x = x.to(device)
                y = y.to(device)

                optimizer.zero_grad()

                with torch.set_grad_enabled(phase == 'train'):
                    out = model(x)
                    loss = criterion(out, y)

                    if phase == 'train':
                        loss.backward()
                        optimizer.step()
                        scheduler.step()

                running_loss += loss.item() * y.size(0)
                running_total += y.size(0)

            epoch_loss = running_loss / running_total
            print(f'{phase.capitalize()} Loss: {epoch_loss}')
            losses_data[phase].append(epoch_loss)
    return losses_data

In [125]:
epochs = 50
cnn_model = CNN(out_size=1)
dataloader = {
    'train': DataLoader(train_ds, batch_size=128, shuffle=True),
    'valid': DataLoader(valid_ds, batch_size=128)
}
optim = torch.optim.Adam(cnn_model.parameters(), lr=1e-1, weight_decay=1e-3)
sched = torch.optim.lr_scheduler.OneCycleLR(optim, max_lr=1e-3, steps_per_epoch=len(dataloader['train']), epochs=epochs)
criterion = nn.MSELoss()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [126]:
losses = train_model(cnn_model, dataloader, optim, sched, criterion, device, epochs)

  0%|                                                                                           | 0/32 [00:00<?, ?it/s]

Epoch 0/49


 12%|██████████▍                                                                        | 4/32 [00:00<00:00, 34.63it/s]

Train Loss: 0.6346121549250652


  6%|█████▏                                                                             | 2/32 [00:00<00:02, 13.79it/s]

...

  3%|██▌                                                                                | 1/32 [00:00<00:03,  9.16it/s]

Valid Loss: 0.40696403639106715
Epoch 49/49


 12%|██████████▍                                                                        | 4/32 [00:00<00:00, 31.68it/s]

Train Loss: 0.016326337617422325


Valid Loss: 0.38108371384534473


In [128]:
layout = dict(xaxis=dict(title='Epoch'), yaxis=dict(title='Loss'))
fig = go.Figure(layout=layout)
fig.add_trace(go.Scatter(y=losses['train'], mode='lines', name='Train Loss',))
fig.add_trace(go.Scatter(y=losses['valid'], mode='lines', name='Valid Loss'))

In [129]:
# Switching model into evaluation mode
cnn_model = cnn_model.eval()

# Calculation of the predictions for training data
with torch.no_grad():
    res_train = cnn_model(train_ds[:][0].to(device))
res_train = res_train.cpu()

# Calculation of the predictions for validation data
with torch.no_grad():
    res_valid = cnn_model(valid_ds[:][0].to(device))
res_valid = res_valid.cpu()

In [130]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=train['timestamp'], y=train['value'], 
                         mode='markers',name='ground truth',
                         marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=train['timestamp'],
                         y=train['predict'], 
                         mode='markers',name='predicted value',
                         marker=dict(color='orange')))

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=valid['timestamp'], y=valid['value'], 
                         mode='markers',name='ground truth',
                         marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=valid['timestamp'],
                         y=valid['predict'], 
                         mode='markers',name='predicted value',
                         marker=dict(color='orange')))

# Long Short-Term Memory Neural Network:

In [106]:
class CPUDataset(Dataset):
    def __init__(self, data: pd.DataFrame, size: int):
        self.chunks = torch.FloatTensor(data['stand_value']).unfold(0, size, size)
        
    def __len__(self):
        return self.chunks.size(0)
    
    def __getitem__(self, i):
        x = self.chunks[i]
        return x

train_ds = CPUDataset(train, 64)
valid_ds = CPUDataset(valid, 64)

In [107]:
class LSTMModel(nn.Module):
    def __init__(self, in_size, hidden_size, out_size, device):
        super().__init__()
        self.hidden_size = hidden_size
        self.lstm = nn.LSTM(in_size, hidden_size)
        self.linear = nn.Linear(hidden_size, out_size)
        self.device = device
        self.init_hidden()
        
    def forward(self, x):
        out, self.hidden_state = self.lstm(
            x.view(len(x), 1, -1), self.hidden_state
        )
        self.hidden_state = tuple(
            [h.detach() for h in self.hidden_state]
        )
        out = out.view(len(x), -1)
        out = self.linear(out)
        return out
    
    def init_hidden(self):
        self.hidden_state = (
            torch.zeros((1, 1, self.hidden_size)).to(self.device),
            torch.zeros((1, 1, self.hidden_size)).to(self.device))

In [108]:
def train_model(model: LSTMModel, dataloaders: dict, optimizer: torch.optim.Optimizer, 
                scheduler, criterion, device: torch.device, epochs: int):
    losses_data = {'train': [], 'valid': []}
    model.to(device)
    for epoch in range(epochs):
        print(f'Epoch {epoch}/{epochs-1}')
        for phase in ['train', 'valid']:
            if phase == 'train':
                model.train()
            else:
                model.eval()

            running_loss = 0.
            running_total = 0.
            
        # Here changes start
            for idx, sequence in enumerate(dataloaders[phase]):
                value = sequence
                value = value.to(device)

                optimizer.zero_grad()

                with torch.set_grad_enabled(phase == 'train'):
                    out = model(value.view(-1, 1))
                    loss = criterion(out.view(-1), value.view(-1))
        # Here changes end

                    if phase == 'train':
                        loss.backward()
                        optimizer.step()
                        scheduler.step()

                running_loss += loss.item() * out.size(0)
                running_total += out.size(0)

            epoch_loss = running_loss / running_total
            print(f'{phase.capitalize()} Loss: {epoch_loss}')
            losses_data[phase].append(epoch_loss)
    return losses_data

In [109]:
epochs = 50
model = LSTMModel(1, 128, 1, device)
dataloaders = {
    'train': DataLoader(train_ds, batch_size=1),
    'valid': DataLoader(valid_ds, batch_size=1)
}
optim = torch.optim.Adam(params=model.parameters(), lr=1e-3)
sched = torch.optim.lr_scheduler.OneCycleLR(
  optim, max_lr=1e-3, steps_per_epoch=len(dataloaders['train']), epochs=epochs
)
criterion = nn.MSELoss()
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [110]:
losses = train_model(model, dataloaders, optim, sched, criterion, device, epochs)

Epoch 0/49
Train Loss: 0.9274842351201981
Valid Loss: 9.807984102339972
Epoch 1/49
Train Loss: 0.839153376600099
Valid Loss: 8.978499842068505
Epoch 2/49
Train Loss: 0.660488348158579
Valid Loss: 6.928682058576554
Epoch 3/49
Train Loss: 0.0807980694068921
Valid Loss: 2.3914287277453004
Epoch 4/49
Train Loss: 0.07264868629031948
Valid Loss: 2.4769443627151233
Epoch 5/49
Train Loss: 0.04673295231565597
Valid Loss: 2.64144859389062
Epoch 6/49
Train Loss: 0.04081485432291788
Valid Loss: 2.6113968309724616
Epoch 7/49
Train Loss: 0.05140312655001051
Valid Loss: 2.8864285078136223
Epoch 8/49
Train Loss: 0.06481872857104809
Valid Loss: 2.83573654926722
Epoch 9/49
Train Loss: 0.07882539639692931
Valid Loss: 2.667318197824652
Epoch 10/49
Train Loss: 0.06727266299080044
Valid Loss: 2.704647759951296
Epoch 11/49
Train Loss: 0.04125916458562844
Valid Loss: 2.692615191910475
Epoch 12/49
Train Loss: 0.0338555355371523
Valid Loss: 2.6811779572791052
Epoch 13/49
Train Loss: 0.03086674804355772
Valid Lo

In [111]:
layout = dict(xaxis=dict(title='Epoch'), yaxis=dict(title='Loss'))
fig = go.Figure(layout=layout)
fig.add_trace(go.Scatter(y=losses['train'], mode='lines', name='Train Loss',))
fig.add_trace(go.Scatter(y=losses['valid'], mode='lines', name='Valid Loss'))

In [112]:
train_values = train['stand_value'].values.astype(np.float32).flatten()
valid_values = valid['stand_value'].values.astype(np.float32).flatten()

In [113]:
# Switching model into evaluation mode
model.eval()

# Calculation of the predictions for training data
with torch.no_grad():
    res_train = model(torch.tensor(train_values).to(device))
res_train = res_train.cpu()

# Calculation of the predictions for validation data
with torch.no_grad():
    res_valid = model(torch.tensor(valid_values).to(device))
res_valid = res_valid.cpu()

In [114]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=train['timestamp'], y=train['value'], 
                         mode='markers',name='ground truth',
                         marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=train['timestamp'],
                         y=train['predict'], 
                         mode='markers',name='predicted value',
                         marker=dict(color='orange')))

In [116]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=valid['timestamp'], y=valid['value'], 
                         mode='markers',name='ground truth',
                         marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=valid['timestamp'],
                         y=valid['predict'], 
                         mode='markers',name='predicted value',
                         marker=dict(color='orange')))